<a href="https://colab.research.google.com/github/jucarmonao/SyS/blob/main/Ecualizador_Juna_Pablo_Carmona_Osorio.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
! pip install youtube-dl  &> /dev/null

In [2]:
!pip install soundfile  &> /dev/null

In [4]:
from scipy.signal import lfilter
from scipy.signal import ellip
from scipy import fft, arange
from IPython.display import Audio
import soundfile as sf 
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
import numpy as np
import matplotlib.pyplot as plt
from scipy.io import wavfile
import os

def espectro(x, sf):

    x = x - np.average(x)  ## Se centra

    n = len(x)
    print(n)
    k = arange(n)
    tarr = n / float(sf)
    frqarr = k / float(tarr)  # dos lados del rango de frecuencia

    frqarr = frqarr[range(n // 2)]  # un lado del rango de frecuencia

    x = fft(x) / n  # Se hace la transformada y se normaliza
    x = x[range(n // 2)]

    return frqarr, abs(x)

def filtro(Link,Frecuencia_Critica,Atenuacion,Tipo_Filtro):
 link=Link
 ! youtube-dl --extract-audio -o "audio2.%(mp3)s" --audio-format mp3  {link}  &> /dev/null

 !ffmpeg -i audio2.mp3 -y output2.wav  &> /dev/null
 nombre_out = "output2.wav"
 x, fs = sf.read(nombre_out)
 x2 = x.copy()
 ti = 63
 tf = ti + 15
 xs = x2[int(ti*fs):int((tf*fs)),:]
 K= int(len(xs)/2) + 1
 print("Segmento de audio original:")
 display(Audio([xs[:,1], xs[:,0]],rate=fs)) #segmento de audio
 filtro = Tipo_Filtro
 N = 6
 frec = Frecuencia_Critica

 ripple_pass = 2
 ripple_stop = Atenuacion
 num, den = ellip(N, rp=ripple_pass, rs=ripple_stop, Wn=frec, btype=filtro, fs=fs) 
 xf = lfilter(num, den, xs, axis=0)
 

 y = x[:, 0]
 y2 = xf[:, 0]
 frq, X = espectro(y, fs)
 frq2, X2 = espectro(y2, fs)

 plt.plot(frq, X, 'b')
 plt.plot(frq2, X2, 'r')
 plt.xlabel('Freq (Hz)')
 plt.ylabel('|X(freq)|')
 plt.tight_layout()
 
 plt.show()
 print("Segmento de audio filtrado:")
 display(Audio([xf[:,1], xf[:,0]],rate=fs)) #Resultado 
 sf.write('sonido_filtrado.wav', xf, fs)
 !ffmpeg -i sonido_filtrado.wav -y sonido_filtrado.mp3  &> /dev/null
 print("El audio filtrado está listo para descargar en MP3: sonido_filtrado.mp3")

In [7]:
programa = interactive(filtro,{'manual': True},Link="https://www.youtube.com/watch?v=AZRPgLxvxKk",Frecuencia_Critica=(0,10000,100),Atenuacion=widgets.IntSlider(min=0, max=101, step=1, value=101),Tipo_Filtro=["highpass","lowpass"])

In [8]:
programa

interactive(children=(Text(value='https://www.youtube.com/watch?v=AZRPgLxvxKk', description='Link'), IntSlider…